In [26]:
import MDAnalysis as mda
from MDAnalysis.analysis.dihedrals import Dihedral, Ramachandran, Janin
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import pandas as pd

# CONTROLS

In [27]:
def get_gyration(directory, topol, traj):
    uni = mda.Universe(f'{directory}/{topol}', f'{directory}/{traj}')
    gyration = []
    print(list(uni.atoms.residues))
    print(uni.masses)
    vnames = [name for name in globals() if globals()[name] is topol]
    print(f'{vnames} contains {uni.trajectory.n_frames} frames')    
    for ts in uni.trajectory:
        #print(f'{ts.frame} out of {uni.trajectory.n_frames}')
        #gyration.append(uni.atoms.radius_of_gyration())
        gyration.append(uni.atoms.radius_of_gyration())

    return gyration

In [28]:
def read_gyration_df(path, gyr_name):
    gyration_df = pd.read_csv(f'{path}/gyrate_{gyr_name}.xvg', sep = '\\s+', header=None, skiprows=[i for i in range(0, 27)])
    gyration_df.columns = ['time', 'gyr', 'g', 'h', 'j']
    gyration_df.drop(['g', 'h', 'j'], axis=1, inplace = True)
    gyration_df['time'] = gyration_df['time']/1000

    return gyration_df

In [29]:
markov_dir = '/home/emanuele/ABeta/markov'
markov_structure = 'reduced-noh.gro'
markov_trajectory = 'traj_red_noh.xtc'
generate_gyr = 'no'
gyr_name = 'markov'
markov_mat = pd.read_csv(f'{markov_dir}/mat.dat', header=None, sep = '\s+')
markov_mat.columns = ['ai', 'aj', 'distance', 'probability']


gmx_gyrate_string = f'echo -e "4\n" | gmx_mpi gyrate -f {markov_dir}/{markov_trajectory} -s {markov_dir}/{markov_structure} -o {markov_dir}/gyrate_{gyr_name}.xvg'

if generate_gyr == 'yes':
    !{gmx_gyrate_string}

markov_gyr = read_gyration_df(markov_dir, gyr_name)
#markov_gyr['gyr'].mean()

In [30]:
greta_random_coil_native_dir = '/home/emanuele/ABeta/random_coil/monomer_test/native_278K'
greta_random_coil_native_structure = 'box_abeta_greta.gro'
greta_random_coil_native_trajectory = 'nopbc_prod.xtc'
generate_gyr = 'no'
gyr_name = 'greta_e_random_coil_native'


greta_random_coil_native_mat = pd.read_csv(f'{greta_random_coil_native_dir}/mat.dat', header=None, sep = '\s+')
greta_random_coil_native_mat.columns = ['ai', 'aj', 'distance', 'probability']


gmx_gyrate_string = f'echo -e "4\n" | gmx_mpi gyrate -f {greta_random_coil_native_dir}/{greta_random_coil_native_trajectory} -s {greta_random_coil_native_dir}/{greta_random_coil_native_structure} -o {greta_random_coil_native_dir}/gyrate_{gyr_name}.xvg'

if generate_gyr == 'yes':
    !{gmx_gyrate_string}

greta_random_coil_native_gyr = read_gyration_df(greta_random_coil_native_dir, gyr_name)
greta_random_coil_native_gyr['gyr'].mean()

2.386732514514912

# TESTS

In [31]:
greta_dir = '/home/emanuele/ABeta/greta_co5.5_ex2/epsilon_310/monomer_test/native_278K'
greta310_carlo_structure = 'prod_abeta_greta.tpr'
greta310_carlo_trajectory = 'prod_abeta_greta.xtc'
generate_gyr = 'no'
gyr_name = 'greta_e310_carlo'


gmx_pbc_string = f'echo -e "0\n" | gmx_mpi trjconv -f {greta_dir}/{greta310_carlo_trajectory} -s {greta_dir}/{greta310_carlo_structure} -pbc mol -o {greta_dir}/nopbc_prod_{gyr_name}.xtc'
gmx_gyrate_string = f'echo -e "4\n" | gmx_mpi gyrate -f {greta_dir}/nopbc_prod_{gyr_name}.xtc -s {greta_dir}/{greta310_carlo_structure} -o {greta_dir}/gyrate_{gyr_name}.xvg'
gmx_mdmat_string = f'echo -e "2\n" | gmx_mpi mdmat -f prod_abeta_greta.xtc -s prod_abeta_greta.tpr'

if generate_gyr == 'yes':
    !{gmx_pbc_string}
    !{gmx_gyrate_string}
    print(gmx_gyrate_string)
    %cd {greta_dir}
    !{gmx_mdmat_string}

greta_310_carlo_mat = pd.read_csv(f'{greta_dir}/mat.dat', header=None, sep = '\s+')
greta_310_carlo_mat.columns = ['ai', 'aj', 'distance', 'probability']

greta_310_carlo_gyr = read_gyration_df(greta_dir, gyr_name)
#greta_310_carlo_gyr['gyr'].mean()
greta_310_carlo_mat

ai  aj  distance  probability
0      1   1  0.000000     1.000000
1      1   2  0.134971     1.000000
2      1   3  0.392171     1.000000
3      1   4  0.612067     0.280464
4      1   5  0.803625     0.157071
...   ..  ..       ...          ...
1759  42  38  0.919923     0.023833
1760  42  39  0.633319     0.190751
1761  42  40  0.378166     1.000000
1762  42  41  0.135379     1.000000
1763  42  42  0.000000     1.000000

[1764 rows x 4 columns]

In [32]:
import plotly.figure_factory as ff
import numpy as np



group_data = [markov_gyr['gyr'], greta_310_carlo_gyr['gyr']]
group_labels = ['markov', '310']


#colors = ['rgb(230, 142, 204)', 'rgb(35, 181, 230)', 'rgb(230, 149, 101)', 'rgb(230, 205, 88)', 'rgb(65, 230, 175)']

fig = ff.create_distplot(group_data, group_labels, bin_size=.01, show_rug=False)#, colors=colors)
fig.update_layout(autosize = False , width = 800, height = 800, plot_bgcolor = 'white', font = dict(size = 30))#, legend  = dict(yanchor = 'top', y = 0.99, xanchor = 'left', x = 0.01))
fig.update_yaxes(title = 'pdf', showline = True, linecolor = 'black', rangemode = 'tozero', showticklabels = False)
fig.update_xaxes(title = 'Radius of gyration (nm)', showline = True, linecolor = 'black')

#fig.write_image("gyr_histograms.png")
fig.show()


In [33]:
def prepare_plotly_heatmap(df):
    return {'z': df.probability.tolist(),
            'x': df.ai.tolist(),
            'y': df.aj.tolist()}

group_labels = ['', 'Charm22', '280 - markov' ,
'280 all pairs', '270 pe21 nm', '270 repulsive']

fig = make_subplots(rows = 2, cols = 3, subplot_titles=group_labels)
fig.add_trace(go.Heatmap(prepare_plotly_heatmap(markov_mat)), row=1, col=2)
#fig.add_trace(go.Heatmap(prepare_plotly_heatmap(greta_random_coil_native_mat)), row=1, col=2)
fig.add_trace(go.Heatmap(prepare_plotly_heatmap(greta_310_carlo_mat)), row=2, col=2)

fig.update_traces(showscale=False)
#fig.add_trace(go.Heatmap(prepare_plotly_heatmap(diff_280_1)), row=1, col=3)




fig.update_layout(width=1800, height=1000, font=dict(size=20))
fig.update_annotations(font_size=25)


In [34]:
diff_310 = greta_310_carlo_mat.copy()
diff_310['probability'] = diff_310['probability'] - markov_mat['probability']

In [35]:
print(sum(diff_310['probability']*diff_310['probability']))

6.433779054648003
